以下の2つのコードを両方とも実行

In [ ]:
from google.colab import drive 
drive.mount("/content/drive")

In [ ]:
!pip install torch safetensors
!pip install wget

以下のリンク等を任意のものに差し替えてから、以下のコードを実行

In [ ]:
#@title <font size="-0">モデルをダウンロード</font>
#@markdown {Google Drive上のモデル名 or モデルのダウンロードリンク} をカンマ区切りで任意個指定
#@markdown - Drive上のモデル名の場合...My Driveに対する相対パスで指定
#@markdown - ダウンロードリンクの場合...Hugging Face等のダウンロードリンクを右クリック & リンクのアドレスをコピー & 下のリンクの代わりに貼り付け
import shutil
import urllib.parse
import urllib.request
import wget

models = "Please use your own model in place of this example, example.safetensors, https://huggingface.co./stabilityai/stable-diffusion-2-1/resolve/main/v2-1_768-ema-pruned.ckpt" #@param {type:"string"}
models = [m.strip() for m in models.split(",") if not models == ""]
for model in models:
  if 0 < len(urllib.parse.urlparse(model).scheme): # if model is url
    wget.download(model)
    # once the bug on python 3.8 is fixed, replace the above code with the following code
    ## model_data = urllib.request.urlopen(model).read()
    ## with open(os.path.basename(model), mode="wb") as f:
    ##   f.write(model_data)
  elif model.endswith((".ckpt", ".safetensors", ".pt", ".pth")):
    from_ = "/content/drive/MyDrive/" + model
    to_ = "/content/" + model
    shutil.copy(from_, to_)
  else:
    print(f"\"{model}\"はURLではなく、正しい形式のファイルでもありません")

この例のように、SD2.1等の比較的新しいモデルを利用する場合は、以下のコードを実行（さもなくばエラーが出力される）

In [ ]:
!pip install pytorch-lightning

以下の2つのコードから好きな方を選んで実行

メモリ不足でクラッシュする場合は、より小さいモデルを利用するか、有料のハイメモリランタイムを使用すること

In [ ]:
#@title <font size="-0">自分でモデル名を指定する場合</font>
import os
import torch
import safetensors.torch

model = "v2-1_768-ema-pruned.ckpt" #@param {type:"string"}
model_name, model_ext = os.path.splitext(model)
as_fp16 = True #@param {type:"boolean"}
save_directly_to_Google_Drive = True #@param {type:"boolean"}

with torch.no_grad():
  if model_ext == ".safetensors":
    weights = safetensors.torch.load_file(model_name + model_ext, device="cpu")
  elif model_ext == ".ckpt":
    weights = torch.load(model_name + model_ext, map_location=torch.device('cpu'))["state_dict"]
  else:
    raise Exception("対応形式は.ckptと.safetensorsです\n" + f"\"{model}\"は対応形式ではありません")
  if as_fp16:
    model_name = model_name + "-fp16"
    for key in weights.keys():
      weights[key] = weights[key].half()
  if save_directly_to_Google_Drive:
    os.chdir("/content/drive/MyDrive")
    safetensors.torch.save_file(weights, model_name + ".safetensors")
    os.chdir("/content")
  else:
    safetensors.torch.save_file(weights, model_name + ".safetensors")
  del weights

!reset

In [ ]:
#@title <font size="-0">自動で全モデルを変換する場合</font>
import os
import glob
import torch
import safetensors.torch

as_fp16 = True #@param {type:"boolean"}
save_directly_to_Google_Drive = True #@param {type:"boolean"}

with torch.no_grad():
  model_paths = glob.glob(r"/content/*.ckpt") + glob.glob(r"/content/*.safetensors") + glob.glob(r"/content/*.pt") + glob.glob(r"/content/*.pth")
  for model_path in model_paths:
    model_name, model_ext = os.path.splitext(os.path.basename(model_path))
    if model_ext == ".safetensors":
      weights = safetensors.torch.load_file(model_name + model_ext, device="cpu")
    elif model_ext == ".ckpt":
      weights = torch.load(model_name + model_ext, map_location=torch.device('cpu'))["state_dict"]
    else:
      print("対応形式は.ckpt	と.safetensorsです\n" + f"\"{model}\"は対応形式ではありません")
      break
    if as_fp16:
      model_name = model_name + "-fp16"
      for key in weights.keys():
        weights[key] = weights[key].half()
    if save_directly_to_Google_Drive:
      os.chdir("/content/drive/MyDrive")
      safetensors.torch.save_file(weights, model_name + ".safetensors")
      os.chdir("/content")
    else:
      safetensors.torch.save_file(weights, model_name + ".safetensors")
    del weights

!reset

モデルのリンク集: https://huggingface.co./models?other=stable-diffusion 等から好きなモデルを選ぼう